# Marketing Materials to Restaurants
### importing libraries

In [1]:
import numpy as np # library to handle data in a vectorized manner
import pandas as pd # library for data analsysis
from bs4 import BeautifulSoup
import requests # library to handle requests
import json # library to handle JSON files
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

!conda install -c conda-forge geopy --yes
import geopy.geocoders 

!conda install -c conda-forge folium=0.5.0 --yes 
import folium # map rendering library

print('Libraries are imported.')


Solving environment: done


==> WARNING: A newer version of conda exists. <==
  current version: 4.5.11
  latest version: 4.7.5

Please update conda by running

    $ conda update -n base -c defaults conda



## Package Plan ##

  environment location: /home/nbuser/anaconda3_501

  added / updated specs: 
    - geopy


The following packages will be downloaded:

    package                    |            build
    ---------------------------|-----------------
    libgcc-ng-9.1.0            |       hdf63c60_0         8.1 MB
    openssl-1.1.1b             |       h14c3975_1         4.0 MB  conda-forge
    wheel-0.33.4               |           py36_0          34 KB  conda-forge
    readline-8.0               |       hf8c457e_0         441 KB  conda-forge
    _libgcc_mutex-0.1          |             main           3 KB
    tk-8.6.9                   |    hed695b0_1002         3.2 MB  conda-forge
    geographiclib-1.49         |             py_0          32 KB  conda-forge
    libffi-3.2.

### Extracting Data From Web

In [2]:
wikipedia_link='https://en.wikipedia.org/wiki/List_of_postal_codes_of_Canada:_M'
raw_wikipedia_page= requests.get(wikipedia_link).text

# using beautiful soup to parse the HTML/XML codes.
soup = BeautifulSoup(raw_wikipedia_page,'xml')
#print(soup.prettify())

In [3]:
table = soup.find('table')

Postcode      = []
Borough       = []
Neighbourhood = []

# print(table)

# extracting a clean form of the table
for tr_cell in table.find_all('tr'):
    
    counter = 1
    Postcode_var      = -1
    Borough_var       = -1
    Neighbourhood_var = -1
    
    for td_cell in tr_cell.find_all('td'):
        if counter == 1: 
            Postcode_var = td_cell.text
        if counter == 2: 
            Borough_var = td_cell.text
            tag_a_Borough = td_cell.find('a')
            
        if counter == 3: 
            Neighbourhood_var = str(td_cell.text).strip()
            tag_a_Neighbourhood = td_cell.find('a')
            
        counter +=1
        
    if (Postcode_var == 'Not assigned' or Borough_var == 'Not assigned' or Neighbourhood_var == 'Not assigned'): 
        continue
    try:
        if ((tag_a_Borough is None) or (tag_a_Neighbourhood is None)):
            continue
    except:
        pass
    if(Postcode_var == -1 or Borough_var == -1 or Neighbourhood_var == -1):
        continue
        
    Postcode.append(Postcode_var)
    Borough.append(Borough_var)
    Neighbourhood.append(Neighbourhood_var)

In [4]:
unique_p = set(Postcode)
print('num of unique Postal codes:', len(unique_p))
Postcode_u      = []
Borough_u       = []
Neighbourhood_u = []


for postcode_unique_element in unique_p:
    p_var = ''; b_var = ''; n_var = ''; 
    for postcode_idx, postcode_element in enumerate(Postcode):
        if postcode_unique_element == postcode_element:
            p_var = postcode_element;
            b_var = Borough[postcode_idx]
            if n_var == '': 
                n_var = Neighbourhood[postcode_idx]
            else:
                n_var = n_var + ', ' + Neighbourhood[postcode_idx]
    Postcode_u.append(p_var)
    Borough_u.append(b_var)
    Neighbourhood_u.append(n_var)
    toronto_dict = {'Postcode':Postcode_u, 'Borough':Borough_u, 'Neighbourhood':Neighbourhood_u}
df_toronto = pd.DataFrame.from_dict(toronto_dict)
df_toronto.to_csv('toronto_part1.csv')
cord_df= pd.read_csv('http://cocl.us/Geospatial_data')
df_toronto[['Latitude','Longitude']]= cord_df[['Latitude','Longitude']]
df5 = df_toronto

num of unique Postal codes: 77


### Creating a Map

In [5]:
# for the city Toronto, latitude and longtitude are manually extracted via google search
toronto_latitude = 43.6932; toronto_longitude = -79.3832
map_toronto = folium.Map(location = [toronto_latitude, toronto_longitude], zoom_start = 10.7)

# add markers to map
for lat, lng, borough, neighborhood in zip(df_toronto['Latitude'], df5['Longitude'], df_toronto['Borough'], df_toronto['Neighbourhood']):
    label = '{}, {}'.format(neighborhood, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7).add_to(map_toronto)  
    

map_toronto

### Focus on Scarborough Data

In [6]:
scarborough_data = df5[df5['Borough'] == 'Scarborough']
scarborough_data.head()

Postcode      Borough                           Neighbourhood   Latitude  \
4       M1C  Scarborough  Highland Creek, Rouge Hill, Port Union  43.773136   
10      M1L  Scarborough         Clairlea, Golden Mile, Oakridge  43.757410   
14      M1E  Scarborough                  Morningside, West Hill  43.815252   
17      M1N  Scarborough                             Birch Cliff  43.803762   
21      M1S  Scarborough                               Agincourt  43.789053   

    Longitude  
4  -79.239476  
10 -79.273304  
14 -79.284577  
17 -79.363452  
21 -79.408493

### Map of Scarborough

In [7]:
address_scar = 'Scarborough, Toronto'
latitude_scar = 43.773077
longitude_scar = -79.257774
print('The geograpical coordinate of "Scarborough" are: {}, {}.'.format(latitude_scar, longitude_scar))

map_Scarborough = folium.Map(location=[latitude_scar, longitude_scar], zoom_start=11.5)

# add markers to map
for lat, lng, label in zip(scarborough_data['Latitude'], scarborough_data['Longitude'], scarborough_data['Neighbourhood']):
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius = 10,
        popup = label,
        color ='blue',
        fill = True,
        fill_color = '#3186cc',
        fill_opacity = 0.7).add_to(map_Scarborough)  
    
map_Scarborough

The geograpical coordinate of "Scarborough" are: 43.773077, -79.257774.


In [8]:
def foursquare_crawler (postal_code_list, neighborhood_list, lat_list, lng_list, LIMIT = 500, radius = 1000):
    result_ds = []
    counter = 0
    for postal_code, neighborhood, lat, lng in zip(postal_code_list, neighborhood_list, lat_list, lng_list):
         
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, CLIENT_SECRET, VERSION, 
            lat, lng, radius, LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        tmp_dict = {}
        tmp_dict['Postal Code'] = postal_code; tmp_dict['Neighborhood(s)'] = neighborhood; 
        tmp_dict['Latitude'] = lat; tmp_dict['Longitude'] = lng;
        tmp_dict['Crawling_result'] = results;
        result_ds.append(tmp_dict)
        counter += 1
        print('{}.'.format(counter))
        print('Data is Obtained, for the Postal Code {} (and Neighborhoods {}) SUCCESSFULLY.'.format(postal_code, neighborhood))
    return result_ds;

In [9]:
CLIENT_ID = 'VUZX5AZF2UQL4CUSH1JB35EF533QNTSLTR3U5GJW0IWHVU5I' # your Foursquare ID
CLIENT_SECRET = 'RK2DMMBRTI0E2BJFHU1VHSGWR3L3R2USCLFKRVL3BDDGMA5A' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version

### Getting Venue Details

In [10]:
print('Crawling different neighborhoods inside "Scarborough"')
Scarborough_foursquare_dataset = foursquare_crawler(list(scarborough_data['Postcode']),
                                                   list(scarborough_data['Neighbourhood']),
                                                   list(scarborough_data['Latitude']),
                                                   list(scarborough_data['Longitude']),)

Crawling different neighborhoods inside "Scarborough"
1.
Data is Obtained, for the Postal Code M1C (and Neighborhoods Highland Creek, Rouge Hill, Port Union) SUCCESSFULLY.
2.
Data is Obtained, for the Postal Code M1L (and Neighborhoods Clairlea, Golden Mile, Oakridge) SUCCESSFULLY.
3.
Data is Obtained, for the Postal Code M1E (and Neighborhoods Morningside, West Hill) SUCCESSFULLY.
4.
Data is Obtained, for the Postal Code M1N (and Neighborhoods Birch Cliff) SUCCESSFULLY.
5.
Data is Obtained, for the Postal Code M1S (and Neighborhoods Agincourt) SUCCESSFULLY.
6.
Data is Obtained, for the Postal Code M1K (and Neighborhoods Ionview, Kennedy Park) SUCCESSFULLY.
7.
Data is Obtained, for the Postal Code M1B (and Neighborhoods Rouge, Malvern) SUCCESSFULLY.
8.
Data is Obtained, for the Postal Code M1J (and Neighborhoods Scarborough Village) SUCCESSFULLY.
9.
Data is Obtained, for the Postal Code M1M (and Neighborhoods Cliffcrest, Cliffside) SUCCESSFULLY.
10.
Data is Obtained, for the Postal Cod

### Saving Results

In [11]:
import pickle
with open("Scarborough_foursquare_dataset.txt", "wb") as fp:   #Pickling
    pickle.dump(Scarborough_foursquare_dataset, fp)
with open("Scarborough_foursquare_dataset.txt", "rb") as fp:   # Unpickling
    Scarborough_foursquare_dataset = pickle.load(fp)
    
def get_venue_dataset(foursquare_dataset):
    result_df = pd.DataFrame(columns = ['Postal Code', 'Neighborhood', 
                                           'Neighborhood Latitude', 'Neighborhood Longitude',
                                          'Venue', 'Venue Summary', 'Venue Category', 'Distance'])
    # print(result_df)
    
    for neigh_dict in foursquare_dataset:
        postal_code = neigh_dict['Postal Code']; neigh = neigh_dict['Neighborhood(s)']
        lat = neigh_dict['Latitude']; lng = neigh_dict['Longitude']
        print('Number of Venuse in Coordination "{}" Posal Code and "{}" Negihborhood(s) is:'.format(postal_code, neigh))
        print(len(neigh_dict['Crawling_result']))
        
        for venue_dict in neigh_dict['Crawling_result']:
            summary = venue_dict['reasons']['items'][0]['summary']
            name = venue_dict['venue']['name']
            dist = venue_dict['venue']['location']['distance']
            cat =  venue_dict['venue']['categories'][0]['name']
            
            
            # print({'Postal Code': postal_code, 'Neighborhood': neigh, 
            #                   'Neighborhood Latitude': lat, 'Neighborhood Longitude':lng,
            #                   'Venue': name, 'Venue Summary': summary, 
            #                   'Venue Category': cat, 'Distance': dist})
            
            result_df = result_df.append({'Postal Code': postal_code, 'Neighborhood': neigh, 
                              'Neighborhood Latitude': lat, 'Neighborhood Longitude':lng,
                              'Venue': name, 'Venue Summary': summary, 
                              'Venue Category': cat, 'Distance': dist}, ignore_index = True)
            # print(result_df)
    
    return(result_df)


In [12]:
scarborough_venues = get_venue_dataset(Scarborough_foursquare_dataset)

Number of Venuse in Coordination "M1C" Posal Code and "Highland Creek, Rouge Hill, Port Union" Negihborhood(s) is:
30
Number of Venuse in Coordination "M1L" Posal Code and "Clairlea, Golden Mile, Oakridge" Negihborhood(s) is:
46
Number of Venuse in Coordination "M1E" Posal Code and "Morningside, West Hill" Negihborhood(s) is:
24
Number of Venuse in Coordination "M1N" Posal Code and "Birch Cliff" Negihborhood(s) is:
21
Number of Venuse in Coordination "M1S" Posal Code and "Agincourt" Negihborhood(s) is:
31
Number of Venuse in Coordination "M1K" Posal Code and "Ionview, Kennedy Park" Negihborhood(s) is:
29
Number of Venuse in Coordination "M1B" Posal Code and "Rouge, Malvern" Negihborhood(s) is:
28
Number of Venuse in Coordination "M1J" Posal Code and "Scarborough Village" Negihborhood(s) is:
100
Number of Venuse in Coordination "M1M" Posal Code and "Cliffcrest, Cliffside" Negihborhood(s) is:
63
Number of Venuse in Coordination "M1P" Posal Code and "Dorset Park, Scarborough Town Centre, 

### Showing Venues

In [13]:
scarborough_venues.head()

Postal Code                            Neighborhood  Neighborhood Latitude  \
0         M1C  Highland Creek, Rouge Hill, Port Union              43.773136   
1         M1C  Highland Creek, Rouge Hill, Port Union              43.773136   
2         M1C  Highland Creek, Rouge Hill, Port Union              43.773136   
3         M1C  Highland Creek, Rouge Hill, Port Union              43.773136   
4         M1C  Highland Creek, Rouge Hill, Port Union              43.773136   

   Neighborhood Longitude                             Venue  \
0              -79.239476               Federick Restaurant   
1              -79.239476                   CANBE Foods Inc   
2              -79.239476          Drupati's Roti & Doubles   
3              -79.239476  The Real McCoy Burgers And Pizza   
4              -79.239476                       Tim Hortons   

          Venue Summary        Venue Category Distance  
0  This spot is popular      Hakka Restaurant      219  
1  This spot is popular     Indian Restaurant      532  
2  This spot is popular  Caribbean Restaurant      291  
3  This spot is popular          Burger Joint      729  
4  This spot is popular           Coffee Shop      670

### Saving...

In [14]:
scarborough_venues.to_csv('scarborough_venues.csv')
scarborough_venues = pd.read_csv('scarborough_venues.csv')

### Summary

In [15]:
neigh_list = list(scarborough_venues['Neighborhood'].unique())
print('Number of Neighborhoods inside Scarborough:')
print(len(neigh_list))
print('List of Neighborhoods inside Scarborough:')
neigh_list

Number of Neighborhoods inside Scarborough:
15
List of Neighborhoods inside Scarborough:


['Highland Creek, Rouge Hill, Port Union',
 'Clairlea, Golden Mile, Oakridge',
 'Morningside, West Hill',
 'Birch Cliff',
 'Agincourt',
 'Ionview, Kennedy Park',
 'Rouge, Malvern',
 'Scarborough Village',
 'Cliffcrest, Cliffside',
 'Dorset Park, Scarborough Town Centre, Wexford Heights',
 'Agincourt North, Milliken',
 'Upper Rouge',
 "Tam O'Shanter",
 'Maryvale, Wexford',
 'Woburn']

In [16]:
neigh_venue_summary = scarborough_venues.groupby('Neighborhood').count()
neigh_venue_summary

Unnamed: 0  Postal Code  \
Neighborhood                                                                  
Agincourt                                                   31           31   
Agincourt North, Milliken                                  100          100   
Birch Cliff                                                 21           21   
Clairlea, Golden Mile, Oakridge                             46           46   
Cliffcrest, Cliffside                                       63           63   
Dorset Park, Scarborough Town Centre, Wexford H...          80           80   
Highland Creek, Rouge Hill, Port Union                      30           30   
Ionview, Kennedy Park                                       29           29   
Maryvale, Wexford                                           35           35   
Morningside, West Hill                                      24           24   
Rouge, Malvern                                              28           28   
Scarborough Village                                        100          100   
Tam O'Shanter                                              100          100   
Upper Rouge                                                100          100   
Woburn                                                      23           23   

                                                    Neighborhood Latitude  \
Neighborhood                                                                
Agincourt                                                              31   
Agincourt North, Milliken                                             100   
Birch Cliff                                                            21   
Clairlea, Golden Mile, Oakridge                                        46   
Cliffcrest, Cliffside                                                  63   
Dorset Park, Scarborough Town Centre, Wexford H...                     80   
Highland Creek, Rouge Hill, Port Union                                 30   
Ionview, Kennedy Park                                                  29   
Maryvale, Wexford                                                      35   
Morningside, West Hill                                                 24   
Rouge, Malvern                                                         28   
Scarborough Village                                                   100   
Tam O'Shanter                                                         100   
Upper Rouge                                                           100   
Woburn                                                                 23   

                                                    Neighborhood Longitude  \
Neighborhood                                                                 
Agincourt                                                               31   
Agincourt North, Milliken                                              100   
Birch Cliff                                                             21   
Clairlea, Golden Mile, Oakridge                                         46   
Cliffcrest, Cliffside                                                   63   
Dorset Park, Scarborough Town Centre, Wexford H...                      80   
Highland Creek, Rouge Hill, Port Union                                  30   
Ionview, Kennedy Park                                                   29   
Maryvale, Wexford                                                       35   
Morningside, West Hill                                                  24   
Rouge, Malvern                                                          28   
Scarborough Village                                                    100   
Tam O'Shanter                                                          100   
Upper Rouge                                                            100   
Woburn                                                                  23   

                                                    Venue  Venue Summar

In [17]:
print('There are {} uniques categories.'.format(len(scarborough_venues['Venue Category'].unique())))

print('Here is the list of different categories:')
list(scarborough_venues['Venue Category'].unique())

There are 189 uniques categories.
Here is the list of different categories:


['Hakka Restaurant',
 'Indian Restaurant',
 'Caribbean Restaurant',
 'Burger Joint',
 'Coffee Shop',
 'Thai Restaurant',
 'Chinese Restaurant',
 'Music Store',
 'Athletics & Sports',
 'Pharmacy',
 'Bank',
 'Bakery',
 'Yoga Studio',
 'Fried Chicken Joint',
 'Wings Joint',
 'Lounge',
 'Grocery Store',
 'Fast Food Restaurant',
 'Asian Restaurant',
 'Rental Car Location',
 'Bus Line',
 'Sporting Goods Shop',
 'Pizza Place',
 'Electronics Store',
 'Gym / Fitness Center',
 'Italian Restaurant',
 'Vietnamese Restaurant',
 'Pet Store',
 'Latin American Restaurant',
 'Beer Store',
 'Sandwich Place',
 'Bowling Alley',
 'Furniture / Home Store',
 'American Restaurant',
 'Bus Station',
 'Light Rail Station',
 'Clothing Store',
 'Plaza',
 'Shoe Store',
 'Park',
 'Intersection',
 'Restaurant',
 'Automotive Shop',
 'Noodle House',
 'Vegetarian / Vegan Restaurant',
 'Event Space',
 'Korean Restaurant',
 'Dessert Shop',
 'Malay Restaurant',
 'Hobby Shop',
 'BBQ Joint',
 'Gym',
 'Shop & Service',
 'Hous

In [18]:
scarborough_onehot = pd.get_dummies(data = scarborough_venues, drop_first  = False, 
                              prefix = "", prefix_sep = "", columns = ['Venue Category'])
scarborough_onehot.head()

Unnamed: 0 Postal Code                            Neighborhood  \
0           0         M1C  Highland Creek, Rouge Hill, Port Union   
1           1         M1C  Highland Creek, Rouge Hill, Port Union   
2           2         M1C  Highland Creek, Rouge Hill, Port Union   
3           3         M1C  Highland Creek, Rouge Hill, Port Union   
4           4         M1C  Highland Creek, Rouge Hill, Port Union   

   Neighborhood Latitude  Neighborhood Longitude  \
0              43.773136              -79.239476   
1              43.773136              -79.239476   
2              43.773136              -79.239476   
3              43.773136              -79.239476   
4              43.773136              -79.239476   

                              Venue         Venue Summary  Distance  \
0               Federick Restaurant  This spot is popular       219   
1                   CANBE Foods Inc  This spot is popular       532   
2          Drupati's Roti & Doubles  This spot is popular       291   
3  The Real McCoy Burgers And Pizza  This spot is popular       729   
4                       Tim Hortons  This spot is popular       670   

   American Restaurant  Antique Shop  Art Gallery  Art Museum  \
0                    0             0            0           0   
1                    0             0            0           0   
2                    0             0            0           0   
3                    0             0            0           0   
4                    0             0            0           0   

   Arts & Crafts Store  Asian Restaurant  Athletics & Sports  Automotive Shop  \
0                    0                 0                   0                0   
1                    0                 0                   0                0   
2                    0                 0                   0                0   
3                    0                 0                   0                0   
4                    0                 0                   0                0   

   BBQ Joint  Bagel Shop  Bakery  Bank  Bar  Baseball Field  Beer Bar  \
0          0           0       0     0    0               0         0   
1          0           0       0     0    0               0         0   
2          0           0       0     0    0               0         0   
3          0           0       0     0    0               0         0   
4          0           0       0     0    0               0         0   

   Beer Store  Belgian Restaurant  Bistro  Bookstore  Boutique  Bowling Alley  \
0           0                   0       0          0         0              0   
1           0                   0       0          0         0              0   
2           0                   0       0          0         0              0   
3           0                   0       0          0         0              0   
4           0                   0       0          0         0              0   

   Breakfast Spot  Brewery  Bridal Shop  Bubble Tea Shop  Burger Joint  \
0               0        0            0                0             0   
1               0        0            0                0             0   
2               0        0            0                0             0   
3               0        0            0                0             1   
4               0        0            0                0             0   

   Burrito Place  Bus Line  Bus Station  Bus Stop  Cafeteria  Café  \
0              0         0            0         0          0     0   
1              0         0            0         0          0     0   
2              0         0            0         0          0     0   
3              0         0            0         0          0     0   
4              0         0            0         0          0     0   

   Candy Store  Cantonese Restaurant  Caribbean Restaurant  Cemetery  \
0            0                     0                     0         0   
1            0                    

In [23]:

important_list_of_features = [
 
 'Neighborhood',
 'Neighborhood Latitude',
 'Neighborhood Longitude',

 'African Restaurant',
 'American Restaurant',
 'Asian Restaurant',

 
 'BBQ Joint',
 
 'Bakery',
 
 
 
 
 
 'Breakfast Spot',

 'Burger Joint',
 
 
 
 'Cajun / Creole Restaurant',
 'Cantonese Restaurant',
 'Caribbean Restaurant',
 'Chinese Restaurant',
 
 'Diner',


 'Fast Food Restaurant',
 'Filipino Restaurant',
 'Fish Market',
 'Food & Drink Shop',
 'Fried Chicken Joint',
 'Fruit & Vegetable Store',
 
 'Greek Restaurant',
 'Grocery Store',
 
 'Hakka Restaurant',
 
 'Hong Kong Restaurant',

 'Hotpot Restaurant',
 
 'Indian Restaurant',

 'Italian Restaurant',
 'Japanese Restaurant',
 'Korean Restaurant',
 'Latin American Restaurant',



 'Malay Restaurant',
 
 'Mediterranean Restaurant',
 
 'Mexican Restaurant',
 'Middle Eastern Restaurant',
 
 'Noodle House',
 
 'Pizza Place',
 
 'Restaurant',
 'Sandwich Place',
 'Seafood Restaurant',
 'Shanghai Restaurant',
 
 'Sushi Restaurant',
 'Taiwanese Restaurant',
 
 'Thai Restaurant',
 
 'Vegetarian / Vegan Restaurant',
 
 'Vietnamese Restaurant',
 'Wings Joint']

In [34]:

scarborough_onehot = scarborough_onehot[important_list_of_features].drop(columns = ['Neighborhood Latitude', 'Neighborhood Longitude']).groupby('Neighborhood').sum()


scarborough_onehot

KeyError: "['African Restaurant' 'American Restaurant' 'Asian Restaurant' 'BBQ Joint'\n 'Burger Joint' 'Cajun / Creole Restaurant' 'Cantonese Restaurant'\n 'Caribbean Restaurant' 'Chinese Restaurant' 'Fast Food Restaurant'\n 'Filipino Restaurant' 'Fried Chicken Joint' 'Fruit & Vegetable Store'\n 'Greek Restaurant' 'Hakka Restaurant' 'Hong Kong Restaurant'\n 'Hotpot Restaurant' 'Indian Restaurant' 'Italian Restaurant'\n 'Japanese Restaurant' 'Korean Restaurant' 'Latin American Restaurant'\n 'Malay Restaurant' 'Mediterranean Restaurant' 'Mexican Restaurant'\n 'Middle Eastern Restaurant' 'Restaurant' 'Seafood Restaurant'\n 'Shanghai Restaurant' 'Sushi Restaurant' 'Taiwanese Restaurant'\n 'Thai Restaurant' 'Vegetarian / Vegan Restaurant' 'Vietnamese Restaurant'\n 'Wings Joint'] not in index"

In [29]:
feat_name_list = list(scarborough_onehot.columns)
restaurant_list = []


for counter, value in enumerate(feat_name_list):
    if value.find('Restaurant') != (-1):
        restaurant_list.append(value)
        
scarborough_onehot['Total Restaurants'] = scarborough_onehot[restaurant_list].sum(axis = 1)
scarborough_onehot = scarborough_onehot.drop(columns = restaurant_list)


feat_name_list = list(scarborough_onehot.columns)
joint_list = []


for counter, value in enumerate(feat_name_list):
    if value.find('Joint') != (-1):
        joint_list.append(value)
        
scarborough_onehot['Total Joints'] = scarborough_onehot[joint_list].sum(axis = 1)
scarborough_onehot = scarborough_onehot.drop(columns = joint_list)


/home/nbuser/anaconda3_501/lib/python3.6/site-packages/ipykernel/__main__.py:21: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy


### Data Set

In [22]:

scarborough_onehot

Unnamed: 0 Postal Code  \
0             0         M1C   
1             1         M1C   
2             2         M1C   
3             3         M1C   
4             4         M1C   
5             5         M1C   
6             6         M1C   
7             7         M1C   
8             8         M1C   
9             9         M1C   
10           10         M1C   
11           11         M1C   
12           12         M1C   
13           13         M1C   
14           14         M1C   
15           15         M1C   
16           16         M1C   
17           17         M1C   
18           18         M1C   
19           19         M1C   
20           20         M1C   
21           21         M1C   
22           22         M1C   
23           23         M1C   
24           24         M1C   
25           25         M1C   
26           26         M1C   
27           27         M1C   
28           28         M1C   
29           29         M1C   
30           30         M1L   
31           31         M1L   
32           32         M1L   
33           33         M1L   
34           34         M1L   
35           35         M1L   
36           36         M1L   
37           37         M1L   
38           38         M1L   
39           39         M1L   
40           40         M1L   
41           41         M1L   
42           42         M1L   
43           43         M1L   
44           44         M1L   
45           45         M1L   
46           46         M1L   
47           47         M1L   
48           48         M1L   
49           49         M1L   
50           50         M1L   
51           51         M1L   
52           52         M1L   
53           53         M1L   
54           54         M1L   
55           55         M1L   
56           56         M1L   
57           57         M1L   
58           58         M1L   
59           59         M1L   
60           60         M1L   
61           61         M1L   
62           62         M1L   
63           63         M1L   
64           64         M1L   
65           65         M1L   
66           66         M1L   
67           67         M1L   
68           68         M1L   
69           69         M1L   
70           70         M1L   
71           71         M1L   
72           72         M1L   
73           73         M1L   
74           74         M1L   
75           75         M1L   
76           76         M1E   
77           77         M1E   
78           78         M1E   
79           79         M1E   
80           80         M1E   
81           81         M1E   
82           82         M1E   
83           83         M1E   
84           84         M1E   
85           85         M1E   
86           86         M1E   
87           87         M1E   
88           88         M1E   
89           89         M1E   
90           90         M1E   
91           91         M1E   
92           92         M1E   
93           93         M1E   
94           94         M1E   
95           95         M1E   
96           96         M1E   
97           97         M1E   
98           98         M1E   
99           99         M1E   
100         100         M1N   
101         101         M1N   
102         102         M1N   
103         103         M1N   
104         104         M1N   
105         105         M1N   
106         106         M1N   
107         107         M1N   
108         108         M1N   
109         109         M1N   
110         110         M1N   
111         111         M1N   
112         112         M1N   
113         113         M1N   
114         114         M1N   
115         115         M1N   
116         116         M1N   
117         117         M1N   
118         118         M1N   
119         119         M1N   
120         120         M1N   
121         121         M1S   
122         122         M1S   
123         123         M1S   
124         124         M1S   
125         125         M1S   
126         126         M1S   
127         127         M1S   
128   

### K means clustering

In [30]:
from sklearn.cluster import KMeans

# run k-means clustering
kmeans = KMeans(n_clusters = 5, random_state = 0).fit(scarborough_onehot)

ValueError: could not convert string to float: 'This spot is popular'

In [31]:
means_df = pd.DataFrame(kmeans.cluster_centers_)
means_df.columns = scarborough_onehot.columns
means_df.index = ['G1','G2','G3','G4','G5']
means_df['Total Sum'] = means_df.sum(axis = 1)
means_df.sort_values(axis = 0, by = ['Total Sum'], ascending=False)

NameError: name 'kmeans' is not defined